# rf506_msgservice
Organisation and simultaneous fits: tuning and customizing the RooFit message logging facility




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Monday, December 15, 2025 at 04:23 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooPolynomial.h"
#include "RooAddPdf.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "RooPlot.h"
#include "RooMsgService.h"

using namespace RooFit;

Create pdf
--------------------

Construct gauss(x,m,s)

In [2]:
RooRealVar x("x", "x", -10, 10);
RooRealVar m("m", "m", 0, -10, 10);
RooRealVar s("s", "s", 1, -10, 10);
RooGaussian gauss("g", "g", x, m, s);

[#0] WARNING:InputArguments -- The parameter 's' with range [-10, 10] of the RooGaussian 'g' exceeds the safe range of (0, inf). Advise to limit its range.


Construct poly(x,p0)

In [3]:
RooRealVar p0("p0", "p0", 0.01, 0., 1.);
RooPolynomial poly("p", "p", x, p0);

Construct model = f*gauss(x) + (1-f)*poly(x)

In [4]:
RooRealVar f("f", "f", 0.5, 0., 1.);
RooAddPdf model("model", "model", RooArgSet(gauss, poly), f);

std::unique_ptr<RooDataSet> data{model.generate(x, 10)};

input_line_55:5:1: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
std::unique_ptr<RooDataSet> data{model.generate(x, 10)};
^


Print configuration of message service
---------------------------------------------------------------------------

Print streams configuration

In [5]:
RooMsgService::instance().Print();
cout << endl;

Active Message streams
[0] MinLevel = PROGRESS Topic = Generation Minimization Plotting Fitting Integration LinkStateMgmt Eval Caching Optimization ObjectHandling InputArguments Tracing Contents DataHandling NumericIntegration FastEvaluations 
[1] MinLevel = INFO Topic = Minimization Plotting Fitting Eval Caching ObjectHandling InputArguments DataHandling NumericIntegration 
[2] MinLevel = INFO Topic = HistFactory 



Adding Integration topic to existing INFO stream
-----------------------------------------------------------------------------------------------

Print streams configuration

In [6]:
RooMsgService::instance().Print();
cout << endl;

Active Message streams
[0] MinLevel = PROGRESS Topic = Generation Minimization Plotting Fitting Integration LinkStateMgmt Eval Caching Optimization ObjectHandling InputArguments Tracing Contents DataHandling NumericIntegration FastEvaluations 
[1] MinLevel = INFO Topic = Minimization Plotting Fitting Eval Caching ObjectHandling InputArguments DataHandling NumericIntegration 
[2] MinLevel = INFO Topic = HistFactory 



Add Integration topic to existing INFO stream

In [7]:
RooMsgService::instance().getStream(1).addTopic(Integration);

Construct integral over gauss to demonstrate new message stream

In [8]:
std::unique_ptr<RooAbsReal> igauss{gauss.createIntegral(x)};
igauss->Print();

[#1] INFO:Integration -- RooRealIntegral::ctor(g_Int[x]) Constructing integral of function g over observables(x) with normalization () with range identifier <none>
[#1] INFO:Integration -- g: Observable x is suitable for analytical integration (if supported by p.d.f)
[#1] INFO:Integration -- g: Function integrated observables (x) internally with code 1
[#1] INFO:Integration -- g: Observables (x) are analytically integrated with code 1
RooRealIntegral::g_Int[x][ Int gd[Ana](x) ] = 2.50663


Print streams configuration in verbose, which also shows inactive streams

In [9]:
cout << endl;
RooMsgService::instance().Print();
cout << endl;


Active Message streams
[0] MinLevel = PROGRESS Topic = Generation Minimization Plotting Fitting Integration LinkStateMgmt Eval Caching Optimization ObjectHandling InputArguments Tracing Contents DataHandling NumericIntegration FastEvaluations 
[1] MinLevel = INFO Topic = Minimization Plotting Fitting Integration Eval Caching ObjectHandling InputArguments DataHandling NumericIntegration 
[2] MinLevel = INFO Topic = HistFactory 



Remove stream

In [10]:
RooMsgService::instance().getStream(1).removeTopic(Integration);

Examples of pdf value tracing stream
-----------------------------------------------------------------------

Show DEBUG level message on function tracing, trace RooGaussian only

In [11]:
RooMsgService::instance().addStream(DEBUG, Topic(Tracing), ClassName("RooGaussian"));

Perform a fit to generate some tracing messages

In [12]:
model.fitTo(*data, Verbose(true));

input_line_63:2:15: error: reference to 'data' is ambiguous
 model.fitTo(*data, Verbose(true));
              ^
input_line_55:5:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{model.generate(x, 10)};
                            ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:319:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:290:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:300:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:310:5: note: candidate found 

Reset message service to default stream configuration

In [13]:
RooMsgService::instance().reset();

Show DEBUG level message on function tracing on all objects, redirect output to file

In [14]:
RooMsgService::instance().addStream(DEBUG, Topic(Tracing), OutputFile("rf506_debug.log"));

Perform a fit to generate some tracing messages

In [15]:
model.fitTo(*data, Verbose(true));

input_line_66:2:15: error: reference to 'data' is ambiguous
 model.fitTo(*data, Verbose(true));
              ^
input_line_55:5:29: note: candidate found by name lookup is 'data'
std::unique_ptr<RooDataSet> data{model.generate(x, 10)};
                            ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:319:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:290:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:300:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/lib/gcc/x86_64-redhat-linux/11/../../../../include/c++/11/bits/range_access.h:310:5: note: candidate found 

Reset message service to default stream configuration

In [16]:
RooMsgService::instance().reset();

Example of another debugging stream
---------------------------------------------------------------------

Show DEBUG level messages on client/server link state management

In [17]:
RooMsgService::instance().addStream(DEBUG, Topic(LinkStateMgmt));
RooMsgService::instance().Print("v");

All Message streams
[0] MinLevel = PROGRESS Topic = Generation Minimization Plotting Fitting Integration LinkStateMgmt Eval Caching Optimization ObjectHandling InputArguments Tracing Contents DataHandling NumericIntegration FastEvaluations 
[1] MinLevel = INFO Topic = Minimization Plotting Fitting Eval Caching ObjectHandling InputArguments DataHandling NumericIntegration 
[2] MinLevel = INFO Topic = HistFactory 
[3] MinLevel = DEBUG Topic = LinkStateMgmt 


Clone composite pdf g to trigger some link state management activity

In [18]:
RooAbsArg *gprime = gauss.cloneTree();
gprime->Print();

[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server x(0x7f9134014000) for value 
[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server m(0x7f91340143e8) for value 
[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server s(0x7f91340147d0) for value 
[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server x(0x7f9134014000) for value 
[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server m(0x7f91340143e8) for value 
[#3] DEBUG:LinkStateMgmt -- RooAbsArg::addServer(0x7f910d9380b0,g): adding server s(0x7f91340147d0) for value 
RooGaussian::g[ x=x mean=m sigma=s ] = 1


Reset message service to default stream configuration

In [19]:
RooMsgService::instance().reset();